# Feuille de travaux pratiques. Méthodes itératives de résolution des systèmes linéaires (deuxième partie)

In [ ]:
# chargement des bibliothèques
import numpy as np

%matplotlib inline
import matplotlib.pyplot as plt

Dans cette feuille, on s'intéresse à deux méthodes itératives de résolution de systèmes linéaires, qui diffèrent des [méthodes linéaires stationnaires du premier degré](https://en.wikipedia.org/wiki/Iterative_method#Stationary_iterative_methods) considérees dans le cours et qui font partie des *méthodes de projection*. De conception géométrique, ces dernières utilisent le fait que chaque équation d'un système linéaire peut être vue comme l'équation d'un hyperplan affine, l'ensemble des solutions du système étant alors l'intersection (qui peut être vide si le système est incompatible) d'hyperplans affines. Elles présentent l'avantage d'approcher la solution (de norme minimale) d'un système linéaire sur-déterminé.

## Exercice 1 (méthode de Kaczmarz)
La [méthode de Kaczmarz](https://en.wikipedia.org/wiki/Kaczmarz_method), introduite en 1937, est une méthode itérative de résolution d'un système linéaire $Ax=b$. Soit $m$ et $n$ les nombres respectifs de lignes et de colonnes de la matrice $A$, $b_i$ la $i$<sup>e</sup> composante du vecteur $b$ et $a_i$ la matrice ligne correspondant à la $i$<sup>e</sup> ligne de la matrice $A$, $i=1,\dots,m$. La relation de récurrence définissant la méthode est alors
$$
\forall k\in\mathbb{N},\ x^{(k+1)}=x^{(k)}+\frac{b_i-\left<{a_i}^\top,x^{(k)}\right>}{\|{a_i}^\top\|^2}{a_i}^\top,
$$
où $i=(k \mod m)+1$ et où $\left<\cdot\,,\cdot\right>$ représente le produit scalaire euclidien et $\|\cdot\|$ la norme qui lui est associée, le vecteur initial $x^{(0)}$ étant donné.

Cette méthode a une interprétation géométrique claire. À chaque itération, le nouvel itéré est la projection orthogonale du précedent sur l'hyperplan affine $H_i=\left\{x\in M_{n,1}(\mathbb{R})\,|\,\left<{a_i}^\top,x\right>= b_i\right\}$, associé à la $i$<sup>e</sup> équation du système linéaire. Les $m$ contraintes formant le système linéaire étant utilisées séquentiellement et de manière cyclique, cette version originelle du procédé est parfois appelée la méthode de Kaczmarz *cyclique*. 

On peut montrer que, pour un système linéaire compatible, la méthode converge vers la solution de norme minimale du système si $x^{(0)}=0$.

**1.** Sur le modèle des fonctions écrites dans la précédente feuille, écrire une fonction `cyclic_kaczmarz` mettant en &oelig;uvre la méthode de Kaczmarz cyclique. Afin de permettre une illustration de la méthode dans la suite, on stockera les itérés construits par la méthode dans un tableau de type <tt>array</tt> que l'on ajoutera aux arguments en sortie de fonction.

**2.** On considère le système linéaire sur-déterminé $Ax=b$, à quatre équations et deux inconnues, de matrice et second membre suivants :
$$
A=\begin{pmatrix}-4&1\\2&\frac{1}{2}\\3&\frac{3}{2}\\0&1\end{pmatrix}\text{ et }b=\begin{pmatrix}-2\\3\\6\\2\end{pmatrix}.
$$

In [ ]:
A=np.array([[-4, 1], [2, 0.5], [3, 1.5], [0, 1]])
b=np.array([-2, 3, 6, 2.])

**(a)** Vérifier numériquement que ce système linéaire est compatible, c'est-à-dire qu'il possède au moins une solution, et déterminer sa solution de norme minimale en résolvant les équations normales associées. On pourra pour cela utiliser les fonctions `linalg.matrix_rank` et `linalg.solve` de NumPy.

**(b)** Résoudre le système linéaire considéré par la méthode de Kaczmarz cyclique, en utilisant le vecteur nul pour initialisation et une tolérance pour le critère d'arrêt égale à $10^{-8}$. Représenter sur un graphe la trajectoire des itérés dans le plan $\mathbb{R}^2$ (on pourra se restreindre au domaine $\left[-\frac{1}{2},\frac{5}{2}\right]\times\left[-\frac{1}{2},\frac{5}{2}\right]$), ainsi que les hyperplans affines associés aux équations du système linéaire et la solution précédemment calculée. 

Une version modifiée de la méthode, qui conduit parfois à une convergence plus rapide, consiste à ne pas appliquer de manière cyclique les projections orthogonales mais en en sélectionnant une aléatoirement à chaque itération (voir [cet article](https://doi.org/10.1007/s00041-008-9030-4)) selon la loi de probabilité suivante :
$$
P(\{i=l\})=\frac{\|{a_l}^\top\|^2}{{\|A\|_F}^2},\ l=1,\dots,m,
$$
où $\|A\|_F=\sqrt{\text{tr}(A^\top A)}$ désigne la norme de Frobenius de la matrice $A$. On parle alors de méthode de Kaczmarz *randomisée*.

**3.** Modifier la fonction précédemment écrite en une fonction `randomized_kaczmarz` mettant en &oelig;uvre la méthode de Kaczmarz randomisée. Pour réaliser le tirage d'une projection orthogonale à chaque itération, on pourra utiliser la fonction `choices` de la bibliothèque `random` de Python.

In [ ]:
import random

**4.** Résoudre le système linéaire considéré par la méthode de Kaczmarz randomisée, en utilisant le vecteur nul pour initialisation et une tolérance pour le critère d'arrêt égale à $10^{-8}$. Illustrer graphiquement sa convergence comme précédemment.

Une autre variante, proposée par Motzkin en 1952 pour la résolution de systèmes d'inéquations linéaires et étudiée par Agmon (voir [cet article](https://doi.org/10.4153/CJM-1954-037-2)) et Motzkin et Schoenberg (voir [cet article](https://doi.org/10.4153/CJM-1954-038-x)), consiste à sélectionner à chaque itération la projection orthogonale correspondant à l'égalité du système la plus fortement violée par l'itéré courant (on parle d'approche [gloutonne](https://fr.wikipedia.org/wiki/Algorithme_glouton)). Dans le contexte de la résolution d'un système d'équations linéaires, cela revient à choisir la projection sur l'hyperplan affine le plus éloigné de l'itéré courant. On obtient alors l'itéré suivant en appliquant la projection avec un paramètre de relaxation $\omega$, choisi dans l'intervalle $]0,2]$ (le choix $\omega=1$ correspond à l'application classique de la projection orthogonale, le cas $\omega=2$ à celle d'une *réflexion* (ou symétrie orthogonale)). La méthode résultante a pour relation de récurrence
$$
\forall k\in\mathbb{N},\ x^{(k+1)}=x^{(k)}+\omega\frac{b_i-\left<{a_i}^\top,x^{(k)}\right>}{\|{a_i}^\top\|^2}{a_i}^\top
$$
où $i=\arg\max\{j\in\{1,\dots,m\}\,|\,\lvert b_j-\left<{a_j}^\top,x^{(k)}\right>\rvert\}$ et est appelée la *méthode (de relaxation) de Motzkin*.

**5.** Modifier la fonction précédemment écrite en une fonction `motzkin` mettant en &oelig;uvre la méthode de Motzkin.

**6.** Résoudre le système linéaire considéré par la méthode de Motzkin, en utilisant le vecteur nul pour initialisation et une tolérance pour le critère d'arrêt égale à $10^{-8}$. Illustrer graphiquement sa convergence, en jouant notamment avec la valeur du paramètre de relaxation $\omega$.

Pour finir, on s'intéresse aux facteurs influençant la vitesse de convergence de la méthode de Kaczmarz. On considère pour cela les trois systèmes linéaires à deux équations et deux inconnues suivants
$$
\begin{pmatrix}2&3\\1&5\end{pmatrix}\begin{pmatrix}x_1\\x_2\end{pmatrix}=\begin{pmatrix}\frac{11}{10}\\\frac{9}{10}\end{pmatrix},\ \begin{pmatrix}2&3\\3&-8\end{pmatrix}\begin{pmatrix}x_1\\x_2\end{pmatrix}=\begin{pmatrix}\frac{11}{10}\\\frac{2}{5}\end{pmatrix}\text{ et }\begin{pmatrix}2&3\\3&-2\end{pmatrix}\begin{pmatrix}x_1\\x_2\end{pmatrix}=\begin{pmatrix}\frac{11}{10}\\1\end{pmatrix}.
$$

**7.** Résoudre chaque système en utilisant la méthode de Kaczmarz cyclique et représenter les trajectoires des approximations respectives (on pourra se restreindre au domaine $\left[-\frac{1}{10},\frac{1}{2}\right]\times\left[-\frac{1}{10},\frac{2}{5}\right]$), ainsi que les hyperplans affines associés aux équations du système linéaire. Commenter.


## Exercice 2 (méthode de Cimmino)
Là où la méthode de Kaczmarz utilise des projections orthogonales associées à chacune des équations du système linéaire, la *méthode de Cimmino*, introduite en 1938, utilise des réflexions (ou symétries orthogonales) et les applique *simultanément* (plutôt que *séquentiellement*) avec un facteur de relaxation égal $\frac{1}{m}$. De cette manière, un cycle de calcul de $m$ réflexions se trouve groupé en une seule itération, ce qui fait que la relation de récurrence de la méthode s'écrit, en utilisant les notations de l'exercice précédent,
$$
\forall k\in\mathbb{N},\ x^{(k+1)}=x^{(k)}+A^\top D(b-Ax^{(k)}),
$$
où $D$ est la matrice diagonale définie par
$$
D=\frac{2}{m}\begin{pmatrix}\|{a_1}^\top\|^{-2}&0&\dots&\dots&0\\0&\ddots&\ddots&&\vdots\\\vdots&\ddots&\ddots&\ddots&\vdots\\\vdots&&\ddots&\ddots&0\\0&\dots&\dots&0&\|{a_m}^\top\|^{-2}\end{pmatrix},
$$
le vecteur initial $x^{(0)}$ étant donné.

Cette dernière méthode a elle ausssi une interprétation géométrique : tout nouvel itéré est une combinaison convexe (un barycentre à coefficients positifs) des images de l'itéré courant par les rélexions associées aux équations du système. Pour un système linéaire compatible dont la matrice est de rang strictement plus grand que $1$, ces images appartiennent à la surface d'une boule dont le centre est l'intersection des hyperplans $H_i$, $i=1,\dots,m$, et le barycentre construit à partir d'un itéré se trouve à une distance de cette intersection strictement inférieure à celle de l'intersection avec l'itéré, ce qui entraîne la convergence de la méthode.

La méthode de Cimmino converge généralement plus lentement que la méthode de Kaczmarz cyclique, mais ceci peut se trouver compensé par le fait que les réflexions peuvent être calculées *en paralèlle* si l'on dispose de l'architecture matérielle adéquate.

**1.** Sur le modèle des fonctions écrites pour la méthode de Kaczmarz dans l'exercice précédent, écrire une fonction `cimmino` mettant en &oelig;uvre la Cimmino.

**2.** Utiliser la méthode de Cimmino pour résoudre le système sur-déterminé introduit dans l'exercice précedent et représenter graphiquement la trajectoire des approximations calculées.